In [1]:
%reset -f
import numpy as np
import numpy.ma as ma
import pandas as pd
import scipy as si
import xarray as xr
from netCDF4 import Dataset as Dataset 
import matplotlib as mpl
import matplotlib.pyplot as plt
import matplotlib.dates as mdates
import datetime as dt
import matplotlib.ticker as ticker
from numpy import arange
from netCDF4 import num2date
from datetime import datetime, timedelta
import matplotlib.ticker as mticker
import matplotlib.font_manager as font_manager
import matplotlib.patches as patches
import matplotlib.image as mpimg
from mpl_toolkits.axes_grid1.inset_locator import inset_axes
from matplotlib.offsetbox import TextArea, DrawingArea, OffsetImage, AnnotationBbox

import cartopy.crs as ccrs
from cartopy import config
from cartopy.mpl.ticker import LongitudeFormatter, LatitudeFormatter,LatitudeLocator
from cartopy.util import add_cyclic_point
import cartopy.feature as cfeature
from sidecar import Sidecar
from ipywidgets import IntSlider
import json
from matplotlib import transforms
from cartopy.mpl.geoaxes import GeoAxes
from mpl_toolkits.axes_grid1 import AxesGrid
from mpl_toolkits.axes_grid1 import make_axes_locatable
from mpl_toolkits.axes_grid1 import ImageGrid
import math
import operator
%load_ext ferretmagic

In [6]:
%%ferret 
!Vertical profile general
can da/all
can var/all
can win/all
can sym/all

!data 1 =RCP
use 'Data_esd_cdr_mos_JWu/MOS_RCP4.5/Control_RCP4.5/tsi.02000.01.01.nc'
!data 2 =mos conti
use '/Data_esd_cdr_mos_JWu/MOS_RCP4.5/Normal_MOS/MOS_Conti/tavg.02030.01.01.nc'
!data 3 =mos conti noremi
use 'Data_esd_cdr_mos_JWu/MOS_RCP4.5/Sensitivity_tests/MOS_Conti_NoRe/tavg.02030.01.01.nc'
!data 4 =mos stop
use '/Data_esd_cdr_mos_JWu/MOS_RCP4.5/Normal_MOS/MOS_Stop/tavg.02030.01.01.nc'
!data 5 =mos stop noremi
use '/Data_esd_cdr_mos_JWu/MOS_RCP4.5/Sensitivity_tests/MOS_Stop_NoRe/tavg.02030.01.01.nc'
!data 6 =mos au stop
use '/Data_esd_cdr_mos_JWu/MOS_RCP4.5/Sensitivity_tests/MOS_AU_Stop/tavg.02030.01.01.nc'
!data 7 =mos au conti
use '/Data_esd_cdr_mos_JWu/MOS_RCP4.5/Sensitivity_tests/MOS_AU_Conti/tavg.02030.01.01.nc'

def symbol tracer1=dic
def symbol tracer2=po4
def symbol tracer3=no3
def symbol tracer4=o2
def symbol tracer5=phytnpp


In [7]:
%%ferret
can symbol exp,d
def symbol exp=rcp
def symbol d=1
set da ($d)
let mask = G_MSKHR[g=O_($tracer1)@nrst,d=($d)]
let ($exp)_global_($tracer1)=O_($tracer1)[d=($d)]
let ($exp)_atlantic_($tracer1)= if MASK[g=O_($tracer1),d=($d)] eq 1 then O_($tracer1)[d=($d)]
let ($exp)_pacific_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 2 then O_($tracer1)[d=($d)]
let ($exp)_indian_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 3 then O_($tracer1)[d=($d)]
let ($exp)_southern_($tracer1)=O_($tracer1)[d=($d),y=90s:40s]


let ($exp)_global_($tracer2)=O_($tracer2)[d=($d)]
let ($exp)_atlantic_($tracer2)= if MASK[g=O_($tracer2),d=($d)] eq 1 then O_($tracer2)[d=($d)]
let ($exp)_pacific_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 2 then O_($tracer2)[d=($d)]
let ($exp)_indian_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 3 then O_($tracer2)[d=($d)]
let ($exp)_southern_($tracer2)=O_($tracer2)[d=($d),y=90s:40s]

let ($exp)_global_($tracer3)=O_($tracer3)[d=($d)]
let ($exp)_atlantic_($tracer3)= if MASK[g=O_($tracer3),d=($d)] eq 1 then O_($tracer3)[d=($d)]
let ($exp)_pacific_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 2 then O_($tracer3)[d=($d)]
let ($exp)_indian_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 3 then O_($tracer3)[d=($d)]
let ($exp)_southern_($tracer3)=O_($tracer3)[d=($d),y=90s:40s]

let ($exp)_global_($tracer4)=O_($tracer4)[d=($d)]
let ($exp)_atlantic_($tracer4)= if MASK[g=O_($tracer4),d=($d)] eq 1 then O_($tracer4)[d=($d)]
let ($exp)_pacific_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 2 then O_($tracer4)[d=($d)]
let ($exp)_indian_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 3 then O_($tracer4)[d=($d)]
let ($exp)_southern_($tracer4)=O_($tracer4)[d=($d),y=90s:40s]

let ($exp)_global_($tracer5)=O_($tracer5)[d=($d)]
let ($exp)_atlantic_($tracer5)= if MASK[g=O_($tracer5),d=($d)] eq 1 then O_($tracer5)[d=($d)]
let ($exp)_pacific_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 2 then O_($tracer5)[d=($d)]
let ($exp)_indian_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 3 then O_($tracer5)[d=($d)]
let ($exp)_southern_($tracer5)=O_($tracer5)[d=($d),y=90s:40s]

In [8]:
%%ferret 
def symbol cal=[i=@ave,j=@ave,d=($d)]

save/file=avg_vertical.nc ($exp)_global_($tracer1)($cal),($exp)_atlantic_($tracer1)($cal),($exp)_pacific_($tracer1)($cal),($exp)_indian_($tracer1)($cal),($exp)_southern_($tracer1)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer2)($cal),($exp)_atlantic_($tracer2)($cal),($exp)_pacific_($tracer2)($cal),($exp)_indian_($tracer2)($cal),($exp)_southern_($tracer2)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer3)($cal),($exp)_atlantic_($tracer3)($cal),($exp)_pacific_($tracer3)($cal),($exp)_indian_($tracer3)($cal),($exp)_southern_($tracer3)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer4)($cal),($exp)_atlantic_($tracer4)($cal),($exp)_pacific_($tracer4)($cal),($exp)_indian_($tracer4)($cal),($exp)_southern_($tracer4)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer5)($cal),($exp)_atlantic_($tracer5)($cal),($exp)_pacific_($tracer5)($cal),($exp)_indian_($tracer5)($cal),($exp)_southern_($tracer5)($cal)

In [9]:
%%ferret
can symbol exp,d
def symbol exp=mos_conti
def symbol d=2
set da ($d)
let mask = G_MSKHR[g=O_($tracer1)@nrst,d=($d)]
let ($exp)_global_($tracer1)=O_($tracer1)[d=($d)]
let ($exp)_atlantic_($tracer1)= if MASK[g=O_($tracer1),d=($d)] eq 1 then O_($tracer1)[d=($d)]
let ($exp)_pacific_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 2 then O_($tracer1)[d=($d)]
let ($exp)_indian_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 3 then O_($tracer1)[d=($d)]
let ($exp)_southern_($tracer1)=O_($tracer1)[d=($d),y=90s:40s]

let ($exp)_global_($tracer2)=O_($tracer2)[d=($d)]
let ($exp)_atlantic_($tracer2)= if MASK[g=O_($tracer2),d=($d)] eq 1 then O_($tracer2)[d=($d)]
let ($exp)_pacific_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 2 then O_($tracer2)[d=($d)]
let ($exp)_indian_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 3 then O_($tracer2)[d=($d)]
let ($exp)_southern_($tracer2)=O_($tracer2)[d=($d),y=90s:40s]

let ($exp)_global_($tracer3)=O_($tracer3)[d=($d)]
let ($exp)_atlantic_($tracer3)= if MASK[g=O_($tracer3),d=($d)] eq 1 then O_($tracer3)[d=($d)]
let ($exp)_pacific_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 2 then O_($tracer3)[d=($d)]
let ($exp)_indian_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 3 then O_($tracer3)[d=($d)]
let ($exp)_southern_($tracer3)=O_($tracer3)[d=($d),y=90s:40s]

let ($exp)_global_($tracer4)=O_($tracer4)[d=($d)]
let ($exp)_atlantic_($tracer4)= if MASK[g=O_($tracer4),d=($d)] eq 1 then O_($tracer4)[d=($d)]
let ($exp)_pacific_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 2 then O_($tracer4)[d=($d)]
let ($exp)_indian_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 3 then O_($tracer4)[d=($d)]
let ($exp)_southern_($tracer4)=O_($tracer4)[d=($d),y=90s:40s]

let ($exp)_global_($tracer5)=O_($tracer5)[d=($d)]
let ($exp)_atlantic_($tracer5)= if MASK[g=O_($tracer5),d=($d)] eq 1 then O_($tracer5)[d=($d)]
let ($exp)_pacific_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 2 then O_($tracer5)[d=($d)]
let ($exp)_indian_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 3 then O_($tracer5)[d=($d)]
let ($exp)_southern_($tracer5)=O_($tracer5)[d=($d),y=90s:40s]


In [10]:
%%ferret
def symbol cal=[i=@ave,j=@ave,d=($d)]
save/file=avg_vertical.nc/append ($exp)_global_($tracer1)($cal),($exp)_atlantic_($tracer1)($cal),($exp)_pacific_($tracer1)($cal),($exp)_indian_($tracer1)($cal),($exp)_southern_($tracer1)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer2)($cal),($exp)_atlantic_($tracer2)($cal),($exp)_pacific_($tracer2)($cal),($exp)_indian_($tracer2)($cal),($exp)_southern_($tracer2)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer3)($cal),($exp)_atlantic_($tracer3)($cal),($exp)_pacific_($tracer3)($cal),($exp)_indian_($tracer3)($cal),($exp)_southern_($tracer3)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer4)($cal),($exp)_atlantic_($tracer4)($cal),($exp)_pacific_($tracer4)($cal),($exp)_indian_($tracer4)($cal),($exp)_southern_($tracer4)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer5)($cal),($exp)_atlantic_($tracer5)($cal),($exp)_pacific_($tracer5)($cal),($exp)_indian_($tracer5)($cal),($exp)_southern_($tracer5)($cal)

In [11]:
%%ferret
can symbol exp,d
def symbol exp=mos_stop
def symbol d=4
set da ($d)
let mask = G_MSKHR[g=O_($tracer1)@nrst,d=($d)]
let ($exp)_global_($tracer1)=O_($tracer1)[d=($d)]
let ($exp)_atlantic_($tracer1)= if MASK[g=O_($tracer1),d=($d)] eq 1 then O_($tracer1)[d=($d)]
let ($exp)_pacific_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 2 then O_($tracer1)[d=($d)]
let ($exp)_indian_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 3 then O_($tracer1)[d=($d)]
let ($exp)_southern_($tracer1)=O_($tracer1)[d=($d),y=90s:40s]

let ($exp)_global_($tracer2)=O_($tracer2)[d=($d)]
let ($exp)_atlantic_($tracer2)= if MASK[g=O_($tracer2),d=($d)] eq 1 then O_($tracer2)[d=($d)]
let ($exp)_pacific_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 2 then O_($tracer2)[d=($d)]
let ($exp)_indian_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 3 then O_($tracer2)[d=($d)]
let ($exp)_southern_($tracer2)=O_($tracer2)[d=($d),y=90s:40s]

let ($exp)_global_($tracer3)=O_($tracer3)[d=($d)]
let ($exp)_atlantic_($tracer3)= if MASK[g=O_($tracer3),d=($d)] eq 1 then O_($tracer3)[d=($d)]
let ($exp)_pacific_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 2 then O_($tracer3)[d=($d)]
let ($exp)_indian_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 3 then O_($tracer3)[d=($d)]
let ($exp)_southern_($tracer3)=O_($tracer3)[d=($d),y=90s:40s]

let ($exp)_global_($tracer4)=O_($tracer4)[d=($d)]
let ($exp)_atlantic_($tracer4)= if MASK[g=O_($tracer4),d=($d)] eq 1 then O_($tracer4)[d=($d)]
let ($exp)_pacific_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 2 then O_($tracer4)[d=($d)]
let ($exp)_indian_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 3 then O_($tracer4)[d=($d)]
let ($exp)_southern_($tracer4)=O_($tracer4)[d=($d),y=90s:40s]

let ($exp)_global_($tracer5)=O_($tracer5)[d=($d)]
let ($exp)_atlantic_($tracer5)= if MASK[g=O_($tracer5),d=($d)] eq 1 then O_($tracer5)[d=($d)]
let ($exp)_pacific_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 2 then O_($tracer5)[d=($d)]
let ($exp)_indian_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 3 then O_($tracer5)[d=($d)]
let ($exp)_southern_($tracer5)=O_($tracer5)[d=($d),y=90s:40s]



In [12]:
%%ferret
def symbol cal=[i=@ave,j=@ave,d=($d)]
save/file=avg_vertical.nc/append ($exp)_global_($tracer1)($cal),($exp)_atlantic_($tracer1)($cal),($exp)_pacific_($tracer1)($cal),($exp)_indian_($tracer1)($cal),($exp)_southern_($tracer1)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer2)($cal),($exp)_atlantic_($tracer2)($cal),($exp)_pacific_($tracer2)($cal),($exp)_indian_($tracer2)($cal),($exp)_southern_($tracer2)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer3)($cal),($exp)_atlantic_($tracer3)($cal),($exp)_pacific_($tracer3)($cal),($exp)_indian_($tracer3)($cal),($exp)_southern_($tracer3)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer4)($cal),($exp)_atlantic_($tracer4)($cal),($exp)_pacific_($tracer4)($cal),($exp)_indian_($tracer4)($cal),($exp)_southern_($tracer4)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer5)($cal),($exp)_atlantic_($tracer5)($cal),($exp)_pacific_($tracer5)($cal),($exp)_indian_($tracer5)($cal),($exp)_southern_($tracer5)($cal)

In [13]:
%%ferret
can symbol exp,d
def symbol exp=mos_s_noremi
def symbol d=5
set da ($d)
let mask = G_MSKHR[g=O_($tracer1)@nrst,d=($d)]
let ($exp)_global_($tracer1)=O_($tracer1)[d=($d)]
let ($exp)_atlantic_($tracer1)= if MASK[g=O_($tracer1),d=($d)] eq 1 then O_($tracer1)[d=($d)]
let ($exp)_pacific_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 2 then O_($tracer1)[d=($d)]
let ($exp)_indian_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 3 then O_($tracer1)[d=($d)]
let ($exp)_southern_($tracer1)=O_($tracer1)[d=($d),y=90s:40s]

let ($exp)_global_($tracer2)=O_($tracer2)[d=($d)]
let ($exp)_atlantic_($tracer2)= if MASK[g=O_($tracer2),d=($d)] eq 1 then O_($tracer2)[d=($d)]
let ($exp)_pacific_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 2 then O_($tracer2)[d=($d)]
let ($exp)_indian_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 3 then O_($tracer2)[d=($d)]
let ($exp)_southern_($tracer2)=O_($tracer2)[d=($d),y=90s:40s]

let ($exp)_global_($tracer3)=O_($tracer3)[d=($d)]
let ($exp)_atlantic_($tracer3)= if MASK[g=O_($tracer3),d=($d)] eq 1 then O_($tracer3)[d=($d)]
let ($exp)_pacific_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 2 then O_($tracer3)[d=($d)]
let ($exp)_indian_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 3 then O_($tracer3)[d=($d)]
let ($exp)_southern_($tracer3)=O_($tracer3)[d=($d),y=90s:40s]

let ($exp)_global_($tracer4)=O_($tracer4)[d=($d)]
let ($exp)_atlantic_($tracer4)= if MASK[g=O_($tracer4),d=($d)] eq 1 then O_($tracer4)[d=($d)]
let ($exp)_pacific_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 2 then O_($tracer4)[d=($d)]
let ($exp)_indian_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 3 then O_($tracer4)[d=($d)]
let ($exp)_southern_($tracer4)=O_($tracer4)[d=($d),y=90s:40s]


let ($exp)_global_($tracer5)=O_($tracer5)[d=($d)]
let ($exp)_atlantic_($tracer5)= if MASK[g=O_($tracer5),d=($d)] eq 1 then O_($tracer5)[d=($d)]
let ($exp)_pacific_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 2 then O_($tracer5)[d=($d)]
let ($exp)_indian_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 3 then O_($tracer5)[d=($d)]
let ($exp)_southern_($tracer5)=O_($tracer5)[d=($d),y=90s:40s]

In [14]:
%%ferret
def symbol cal=[i=@ave,j=@ave,d=($d)]
save/file=avg_vertical.nc/append ($exp)_global_($tracer1)($cal),($exp)_atlantic_($tracer1)($cal),($exp)_pacific_($tracer1)($cal),($exp)_indian_($tracer1)($cal),($exp)_southern_($tracer1)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer2)($cal),($exp)_atlantic_($tracer2)($cal),($exp)_pacific_($tracer2)($cal),($exp)_indian_($tracer2)($cal),($exp)_southern_($tracer2)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer3)($cal),($exp)_atlantic_($tracer3)($cal),($exp)_pacific_($tracer3)($cal),($exp)_indian_($tracer3)($cal),($exp)_southern_($tracer3)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer4)($cal),($exp)_atlantic_($tracer4)($cal),($exp)_pacific_($tracer4)($cal),($exp)_indian_($tracer4)($cal),($exp)_southern_($tracer4)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer5)($cal),($exp)_atlantic_($tracer5)($cal),($exp)_pacific_($tracer5)($cal),($exp)_indian_($tracer5)($cal),($exp)_southern_($tracer5)($cal)

In [15]:
%%ferret
can symbol exp,d
def symbol exp=mos_au_stop
def symbol d=6
set da ($d)
let mask = G_MSKHR[g=O_($tracer1)@nrst,d=($d)]
let ($exp)_global_($tracer1)=O_($tracer1)[d=($d)]
let ($exp)_atlantic_($tracer1)= if MASK[g=O_($tracer1),d=($d)] eq 1 then O_($tracer1)[d=($d)]
let ($exp)_pacific_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 2 then O_($tracer1)[d=($d)]
let ($exp)_indian_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 3 then O_($tracer1)[d=($d)]
let ($exp)_southern_($tracer1)=O_($tracer1)[d=($d),y=90s:40s]

let ($exp)_global_($tracer2)=O_($tracer2)[d=($d)]
let ($exp)_atlantic_($tracer2)= if MASK[g=O_($tracer2),d=($d)] eq 1 then O_($tracer2)[d=($d)]
let ($exp)_pacific_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 2 then O_($tracer2)[d=($d)]
let ($exp)_indian_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 3 then O_($tracer2)[d=($d)]
let ($exp)_southern_($tracer2)=O_($tracer2)[d=($d),y=90s:40s]

let ($exp)_global_($tracer3)=O_($tracer3)[d=($d)]
let ($exp)_atlantic_($tracer3)= if MASK[g=O_($tracer3),d=($d)] eq 1 then O_($tracer3)[d=($d)]
let ($exp)_pacific_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 2 then O_($tracer3)[d=($d)]
let ($exp)_indian_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 3 then O_($tracer3)[d=($d)]
let ($exp)_southern_($tracer3)=O_($tracer3)[d=($d),y=90s:40s]

let ($exp)_global_($tracer4)=O_($tracer4)[d=($d)]
let ($exp)_atlantic_($tracer4)= if MASK[g=O_($tracer4),d=($d)] eq 1 then O_($tracer4)[d=($d)]
let ($exp)_pacific_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 2 then O_($tracer4)[d=($d)]
let ($exp)_indian_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 3 then O_($tracer4)[d=($d)]
let ($exp)_southern_($tracer4)=O_($tracer4)[d=($d),y=90s:40s]


let ($exp)_global_($tracer5)=O_($tracer5)[d=($d)]
let ($exp)_atlantic_($tracer5)= if MASK[g=O_($tracer5),d=($d)] eq 1 then O_($tracer5)[d=($d)]
let ($exp)_pacific_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 2 then O_($tracer5)[d=($d)]
let ($exp)_indian_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 3 then O_($tracer5)[d=($d)]
let ($exp)_southern_($tracer5)=O_($tracer5)[d=($d),y=90s:40s]

In [16]:
%%ferret
def symbol cal=[i=@ave,j=@ave,d=($d)]
save/file=avg_vertical.nc/append ($exp)_global_($tracer1)($cal),($exp)_atlantic_($tracer1)($cal),($exp)_pacific_($tracer1)($cal),($exp)_indian_($tracer1)($cal),($exp)_southern_($tracer1)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer2)($cal),($exp)_atlantic_($tracer2)($cal),($exp)_pacific_($tracer2)($cal),($exp)_indian_($tracer2)($cal),($exp)_southern_($tracer2)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer3)($cal),($exp)_atlantic_($tracer3)($cal),($exp)_pacific_($tracer3)($cal),($exp)_indian_($tracer3)($cal),($exp)_southern_($tracer3)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer4)($cal),($exp)_atlantic_($tracer4)($cal),($exp)_pacific_($tracer4)($cal),($exp)_indian_($tracer4)($cal),($exp)_southern_($tracer4)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer5)($cal),($exp)_atlantic_($tracer5)($cal),($exp)_pacific_($tracer5)($cal),($exp)_indian_($tracer5)($cal),($exp)_southern_($tracer5)($cal)

In [19]:
%%ferret
can symbol exp,d
def symbol exp=mos_w1_conti
def symbol d=7
set da ($d)
let mask = G_MSKHR[g=O_($tracer1)@nrst,d=($d)]
let ($exp)_global_($tracer1)=O_($tracer1)[d=($d)]
let ($exp)_atlantic_($tracer1)= if MASK[g=O_($tracer1),d=($d)] eq 1 then O_($tracer1)[d=($d)]
let ($exp)_pacific_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 2 then O_($tracer1)[d=($d)]
let ($exp)_indian_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 3 then O_($tracer1)[d=($d)]
let ($exp)_southern_($tracer1)=O_($tracer1)[d=($d),y=90s:40s]

let ($exp)_global_($tracer2)=O_($tracer2)[d=($d)]
let ($exp)_atlantic_($tracer2)= if MASK[g=O_($tracer2),d=($d)] eq 1 then O_($tracer2)[d=($d)]
let ($exp)_pacific_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 2 then O_($tracer2)[d=($d)]
let ($exp)_indian_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 3 then O_($tracer2)[d=($d)]
let ($exp)_southern_($tracer2)=O_($tracer2)[d=($d),y=90s:40s]

let ($exp)_global_($tracer3)=O_($tracer3)[d=($d)]
let ($exp)_atlantic_($tracer3)= if MASK[g=O_($tracer3),d=($d)] eq 1 then O_($tracer3)[d=($d)]
let ($exp)_pacific_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 2 then O_($tracer3)[d=($d)]
let ($exp)_indian_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 3 then O_($tracer3)[d=($d)]
let ($exp)_southern_($tracer3)=O_($tracer3)[d=($d),y=90s:40s]

let ($exp)_global_($tracer4)=O_($tracer4)[d=($d)]
let ($exp)_atlantic_($tracer4)= if MASK[g=O_($tracer4),d=($d)] eq 1 then O_($tracer4)[d=($d)]
let ($exp)_pacific_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 2 then O_($tracer4)[d=($d)]
let ($exp)_indian_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 3 then O_($tracer4)[d=($d)]
let ($exp)_southern_($tracer4)=O_($tracer4)[d=($d),y=90s:40s]


let ($exp)_global_($tracer5)=O_($tracer5)[d=($d)]
let ($exp)_atlantic_($tracer5)= if MASK[g=O_($tracer5),d=($d)] eq 1 then O_($tracer5)[d=($d)]
let ($exp)_pacific_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 2 then O_($tracer5)[d=($d)]
let ($exp)_indian_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 3 then O_($tracer5)[d=($d)]
let ($exp)_southern_($tracer5)=O_($tracer5)[d=($d),y=90s:40s]

In [20]:
%%ferret
def symbol cal=[i=@ave,j=@ave,d=($d)]
save/file=avg_vertical.nc/append ($exp)_global_($tracer1)($cal),($exp)_atlantic_($tracer1)($cal),($exp)_pacific_($tracer1)($cal),($exp)_indian_($tracer1)($cal),($exp)_southern_($tracer1)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer2)($cal),($exp)_atlantic_($tracer2)($cal),($exp)_pacific_($tracer2)($cal),($exp)_indian_($tracer2)($cal),($exp)_southern_($tracer2)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer3)($cal),($exp)_atlantic_($tracer3)($cal),($exp)_pacific_($tracer3)($cal),($exp)_indian_($tracer3)($cal),($exp)_southern_($tracer3)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer4)($cal),($exp)_atlantic_($tracer4)($cal),($exp)_pacific_($tracer4)($cal),($exp)_indian_($tracer4)($cal),($exp)_southern_($tracer4)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer5)($cal),($exp)_atlantic_($tracer5)($cal),($exp)_pacific_($tracer5)($cal),($exp)_indian_($tracer5)($cal),($exp)_southern_($tracer5)($cal)

In [27]:
%%ferret
can symbol exp,d
def symbol exp=mos_c_noremi
def symbol d=3
set da ($d)
let mask = G_MSKHR[g=O_($tracer1)@nrst,d=($d)]
let ($exp)_global_($tracer1)=O_($tracer1)[d=($d)]
let ($exp)_atlantic_($tracer1)= if MASK[g=O_($tracer1),d=($d)] eq 1 then O_($tracer1)[d=($d)]
let ($exp)_pacific_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 2 then O_($tracer1)[d=($d)]
let ($exp)_indian_($tracer1)=if MASK[g=O_($tracer1),d=($d)] eq 3 then O_($tracer1)[d=($d)]
let ($exp)_southern_($tracer1)=O_($tracer1)[d=($d),y=90s:40s]

let ($exp)_global_($tracer2)=O_($tracer2)[d=($d)]
let ($exp)_atlantic_($tracer2)= if MASK[g=O_($tracer2),d=($d)] eq 1 then O_($tracer2)[d=($d)]
let ($exp)_pacific_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 2 then O_($tracer2)[d=($d)]
let ($exp)_indian_($tracer2)=if MASK[g=O_($tracer2),d=($d)] eq 3 then O_($tracer2)[d=($d)]
let ($exp)_southern_($tracer2)=O_($tracer2)[d=($d),y=90s:40s]

let ($exp)_global_($tracer3)=O_($tracer3)[d=($d)]
let ($exp)_atlantic_($tracer3)= if MASK[g=O_($tracer3),d=($d)] eq 1 then O_($tracer3)[d=($d)]
let ($exp)_pacific_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 2 then O_($tracer3)[d=($d)]
let ($exp)_indian_($tracer3)=if MASK[g=O_($tracer3),d=($d)] eq 3 then O_($tracer3)[d=($d)]
let ($exp)_southern_($tracer3)=O_($tracer3)[d=($d),y=90s:40s]

let ($exp)_global_($tracer4)=O_($tracer4)[d=($d)]
let ($exp)_atlantic_($tracer4)= if MASK[g=O_($tracer4),d=($d)] eq 1 then O_($tracer4)[d=($d)]
let ($exp)_pacific_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 2 then O_($tracer4)[d=($d)]
let ($exp)_indian_($tracer4)=if MASK[g=O_($tracer4),d=($d)] eq 3 then O_($tracer4)[d=($d)]
let ($exp)_southern_($tracer4)=O_($tracer4)[d=($d),y=90s:40s]


let ($exp)_global_($tracer5)=O_($tracer5)[d=($d)]
let ($exp)_atlantic_($tracer5)= if MASK[g=O_($tracer5),d=($d)] eq 1 then O_($tracer5)[d=($d)]
let ($exp)_pacific_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 2 then O_($tracer5)[d=($d)]
let ($exp)_indian_($tracer5)=if MASK[g=O_($tracer5),d=($d)] eq 3 then O_($tracer5)[d=($d)]
let ($exp)_southern_($tracer5)=O_($tracer5)[d=($d),y=90s:40s]
set memory/size=5.e12

In [28]:
%%ferret
def symbol cal=[i=@ave,j=@ave,d=($d)]
save/file=avg_vertical.nc/append ($exp)_global_($tracer1)($cal),($exp)_atlantic_($tracer1)($cal),($exp)_pacific_($tracer1)($cal),($exp)_indian_($tracer1)($cal),($exp)_southern_($tracer1)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer2)($cal),($exp)_atlantic_($tracer2)($cal),($exp)_pacific_($tracer2)($cal),($exp)_indian_($tracer2)($cal),($exp)_southern_($tracer2)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer3)($cal),($exp)_atlantic_($tracer3)($cal),($exp)_pacific_($tracer3)($cal),($exp)_indian_($tracer3)($cal),($exp)_southern_($tracer3)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer4)($cal),($exp)_atlantic_($tracer4)($cal),($exp)_pacific_($tracer4)($cal),($exp)_indian_($tracer4)($cal),($exp)_southern_($tracer4)($cal)
save/file=avg_vertical.nc/append ($exp)_global_($tracer5)($cal),($exp)_atlantic_($tracer5)($cal),($exp)_pacific_($tracer5)($cal),($exp)_indian_($tracer5)($cal),($exp)_southern_($tracer5)($cal)

In [8]:
plt.close('all')
d=Dataset('/Users/jjw/Desktop/RCP/4.5_3000/tavg.02000.01.01.nc', 'r')
depth=d.variables['depth']
data=Dataset('./avg_vertical.nc', 'r')

var1 = ["rcp_","mos_conti_","mos_c_noremi_","mos_stop_","mos_s_noremi_","mos_w1_stop_","mos_w1_conti_"]#,"mos_w10_stop_","mos_w10_s_noremi_"]
var2=["global_","atlantic_","pacific_","indian_","southern_"]
var3=["dic","no3","po4","o2"]
var4=["_100","_1000"]
vargroup=[]


vargroup_100=[]
vargroup_1000=[]

for i in var1:
    for j in var2:
        for k in var3:
            name=i+j+k+var4[0]
            vargroup_100.append(name)
for i in var1:
    for j in var2:
        for k in var3:
            name=i+j+k+var4[1]
            vargroup_1000.append(name)   
for i in var1:
    for j in var2:
        for k in var3:
            name=i+j+k
            vargroup.append(name)  
rcp_100=12
rcp_1000=102

mos_100=9
mos_1000=99

oceans=['Global'+'\n Depth(m)','Atlantic Ocean'+'\n Depth(m)','Pacific Ocean'+'\n Depth(m)','Indian Ocean'+'\n Depth(m)','Southern Oceans'+'\n Depth(m)']
tracers=['DIC'+"\n($\mu$mol kg$^{-1}$)",'PO${_4}$'+"\n(mmol m$^{-3}$)",'NO${_3}$'+"\n(mmol m$^{-3}$)",'O${_2}$'+"\n(mmol m$^{-3}$)"]
colors = ['k','#377eb8','#377eb8','#4daf4a', '#4daf4a','#984ea3', '#ff7f00']
linestyles=['-',
         '-','dotted',
         '-','dotted',
        '-','-']
        #'-','-.']
varname  =['Control_RCP4.5',
            'MOS_Conti','MOS_Conti_NoRe',
            'MOS_Stop','MOS_Stop_NoRe',
            'MOS_AU_Stop',
            'MOS_AU_Conti']


fontsize1=30
fontsize2=20
fontsize=30

font = font_manager.FontProperties(family='Serif',style='normal', size=fontsize)
fig,(subgroup)=plt.subplots(5,8,figsize=(45,35))
lw=2.5
tkwx = dict(length=lw,width=lw)
d_100={}
d_1000={}
basins=['GLOBAL','ATLANTIC','PACIFIC','INDIAN','SOUTHERN']
tr=['DIC','PO4','NO3','O2']

linedic=dict(zip(var1,linestyles))
colordic=dict(zip(var1,colors))
labeldic=dict(zip(var1,varname))
for i,name in enumerate(vargroup):
    name=str.upper(vargroup[i])
    name_100=vargroup_100[i]
    name_1000=vargroup_1000[i]
    for j in [0,1,2,3]:
        for k in [0,1,2,3,4]:
            if  operator.contains(name,tr[j]) and operator.contains(name,basins[k]):
                if j==0:
                    if ('RCP' in name):
                            d_100[name_100]=data.variables[name][rcp_100]*1e6/1024.5
                            d_1000[name_1000]=data.variables[name][rcp_1000]*1e6/1024.5
                        
                    else:
                            d_100[name_100]=data.variables[name][mos_100]*1e6/1024.5
                            d_1000[name_1000]=data.variables[name][mos_1000]*1e6/1024.5
                            
                else:
                    if ('RCP' in name):
                            d_100[name_100]=data.variables[name][rcp_100]*1e3
                            d_1000[name_1000]=data.variables[name][rcp_1000]*1e3
                            
                    else:
                            d_100[name_100]=data.variables[name][mos_100]*1e3
                            d_1000[name_1000]=data.variables[name][mos_1000]*1e3

            x=math.ceil(k*8+2*j+1)
            plx=math.ceil(x)
            ply=math.ceil(x+1)
            for i in np.arange(0,7,1):
                if list(colordic.keys())[i] in str.lower(name):
                    color=colordic.get(list(colordic.keys())[i])
                    line=linedic.get(list(colordic.keys())[i])
                    label=labeldic.get(list(colordic.keys())[i])
            ax=plt.subplot(5,8,plx)
            if  operator.contains(name,tr[j]) and operator.contains(name,basins[k]):
                ax.plot(d_100.get(name_100),depth,lw=lw,ls=line,label=label,color=color)#,label=label,ls=line,color=color
            ax=plt.subplot(5,8,ply)
            if  operator.contains(name,tr[j]) and operator.contains(name,basins[k]):   
                ax.plot(d_1000.get(name_1000),depth,lw=lw,ls=line,label=label,color=color)
for i in np.arange(1,41,1):
    ax=plt.subplot(5,8,i)
    ax.tick_params(direction='inout')
    ax.spines['bottom'].set_linewidth(0);
    ax.spines['left'].set_linewidth(lw);
    ax.spines['right'].set_linewidth(0);
    ax.spines['top'].set_linewidth(lw);
    plt.subplots_adjust(wspace =0.2, hspace =0.1)
    ax.invert_yaxis() 
    plt.grid(True,linestyle='--',linewidth=lw)
    ax.tick_params(direction='inout')
    ax.xaxis.set_ticks_position('top')
    #set x limits
    ax=plt.subplot(5,8,i)
    if i in np.arange(1,41,8):
        k=math.ceil(i/8)
        ax=plt.subplot(5,8,i)
        ax.set_ylabel(oceans[k-1],size=fontsize,fontweight='bold')
        ax.tick_params(direction='inout') 
        ax.tick_params(axis='x',**tkwx,labelsize=fontsize2)
        #ax.set_yticklabels(np.arange(0,8000))
        ax.tick_params(axis='y',labelsize=fontsize2)
        ax.set_xlim(2000,2700)
        ax.set_ylim(6000,0)
        ax.tick_params(axis='x',**tkwx,labelsize=fontsize2)
        ax.tick_params(axis='y',labelsize=fontsize)
        if i > 1:
            ax.set_xticklabels([])
    if i in np.arange(2,42,8):
        ax.set_xlim(2000,2700)
        ax.set_ylim(6000,0)
        ax.set_yticklabels([])
        ax.tick_params(axis='x',**tkwx,labelsize=fontsize2)
        ax.tick_params(axis='y',labelsize=fontsize)
        if i > 2:
            ax.set_xticklabels([])
    if i in np.arange(3,43,8) or i in np.arange(4,44,8):
        ax.set_xlim(0,4)
        ax.set_ylim(6000,0)    
        ax.set_yticklabels([])
        ax.tick_params(axis='x',**tkwx,labelsize=fontsize2)
        ax.tick_params(axis='y',labelsize=fontsize)
        if i > 4:
            ax.set_xticklabels([])
    if i in np.arange(5,45,8) or i in np.arange(6,46,8):
        ax.set_xlim(0,50,10)
        ax.set_ylim(6000,0)
        ax.set_yticklabels([])
        ax.tick_params(axis='x',**tkwx,labelsize=fontsize2)
        ax.tick_params(axis='y',labelsize=fontsize)
        if i > 6:
            ax.set_xticklabels([])
    if i in np.arange(7,47,8) or i in np.arange(8,48,8):
        ax.set_xlim(0,300,50)
        ax.set_yticklabels([])
        ax.set_ylim(6000,0)      
        ax.tick_params(axis='x',**tkwx,labelsize=fontsize2)
        ax.tick_params(axis='y',labelsize=fontsize)
        if i > 8:
            ax.set_xticklabels([])
    if i in np.arange(1,9,1):
        ax=plt.subplot(5,8,i)
        if i in [1,3,5,7]:
            k=math.ceil((i-1)/2)
            ax.text(1.1,1.3,tracers[k],size=fontsize,fontweight='bold',horizontalalignment='center',verticalalignment='center', transform=ax.transAxes)
            ax.set_title('\n yr2100',size=fontsize,fontweight='bold')
        else:
            k=math.ceil((i-2)/2)
            ax.set_title('\n yr3000',size=fontsize,fontweight='bold')

handles, labels = ax.get_legend_handles_labels()
display =np.arange(0,11,1)
fig.legend([handle for i,handle in enumerate(handles)if i in display],
          [label for i,label in enumerate(labels)if i in display],bbox_to_anchor=(0.1,0.1),prop={'size':fontsize1,'width':2},loc='upper left',framealpha=0,facecolor='white',ncol=7)

plt.savefig('vertical_profile.pdf',bbox_inches='tight', format='pdf', pad_inches=0.0)
plt.show()

TypeError: __init__() got an unexpected keyword argument 'width'